In [1]:
import pandas as pd
import matplotlib.pyplot as plt
df = pd.read_csv("C://Users//annal//aim//static//csv//Forbes_Billionaires.csv")
print(df.columns)

Index(['Rank ', 'Name', 'Networth', 'Age', 'Country', 'Source', 'Industry'], dtype='object')


# Определим бизнес цели:
## 1- Прогнозирование состояния миллиардера(регрессия)
## 2- Прогнозирование возраста миллиардера(классификация)

# Подготовим данные: удалим колонки rank и name(в них уникальные значения, которые не участвуют в предсказаниях). А также преобразуем номинальные колонки в числовые(country, source, industry) и категоризируем колонку age

In [2]:
# Удаление колонок 'rank' и 'name'
df.drop(columns=['Rank ', 'Name'], inplace=True)

# Проверка, что колонки были удалены
print(df.head())

   Networth  Age        Country              Source                Industry
0     219.0   50  United States       Tesla, SpaceX             Automotive 
1     171.0   58  United States              Amazon             Technology 
2     158.0   73         France                LVMH       Fashion & Retail 
3     129.0   66  United States           Microsoft             Technology 
4     118.0   91  United States  Berkshire Hathaway  Finance & Investments 


In [3]:
from sklearn.preprocessing import OneHotEncoder
from sklearn.feature_extraction.text import TfidfVectorizer

# Преобразуем 'country' и 'industry' в бинарные матрицы с помощью One-Hot Encoding
df_country = pd.get_dummies(df[['Country']], drop_first=True)
df_industry = pd.get_dummies(df[['Industry']], drop_first=True)

# Преобразуем колонку 'source' с помощью TF-IDF
tfidf_vectorizer = TfidfVectorizer(max_features=1000)  
X_tfidf = tfidf_vectorizer.fit_transform(df['Source']).toarray()

# Создаем DataFrame с результатами TF-IDF
df_source_tfidf = pd.DataFrame(X_tfidf, columns=tfidf_vectorizer.get_feature_names_out())

bins = [0, 30, 40, 50, 60, 70, 80, 100]  # границы для возрастных категорий
labels = ['Under 30', '30-40', '40-50', '50-60', '60-70', '70-80', '80+']  # метки для категорий

# Создаем новую колонку 'age_group', где будет храниться категория
df_age_group = pd.cut(df['Age'], bins=bins, labels=labels, right=False)


# Удаляем оригинальные колонки 'country', 'industry' и 'source' из исходного DataFrame
df.drop(columns=['Country', 'Industry', 'Source', 'Age'], inplace=True)

# Объединяем все преобразованные данные в один DataFrame
df_transformed = pd.concat([df, df_country, df_industry, df_source_tfidf, df_age_group], axis=1)

# Просмотр результата
print(df_transformed.head())

   Networth  Country_Argentina  Country_Australia  Country_Austria  \
0     219.0              False              False            False   
1     171.0              False              False            False   
2     158.0              False              False            False   
3     129.0              False              False            False   
4     118.0              False              False            False   

   Country_Barbados  Country_Belgium  Country_Belize  Country_Brazil  \
0             False            False           False           False   
1             False            False           False           False   
2             False            False           False           False   
3             False            False           False           False   
4             False            False           False           False   

   Country_Bulgaria  Country_Canada  ...  wind  wine  winter  wire  wireless  \
0             False           False  ...   0.0   0.0     0.0   0.0

# Разобьём набор данных на обучающую и тестовые выборки (80/20) для задачи классификации. Целевой признак- Age

In [ ]:
from typing import Tuple
import pandas as pd
from pandas import DataFrame
from sklearn.model_selection import train_test_split

def split_stratified_into_train_val_test(
    df_input,
    stratify_colname="y",
    frac_train=0.6,
    frac_val=0.15,
    frac_test=0.25,
    random_state=None,
) -> Tuple[DataFrame, DataFrame, DataFrame, DataFrame, DataFrame, DataFrame]:
   
    if frac_train + frac_val + frac_test != 1.0:
        raise ValueError(
            "fractions %f, %f, %f do not add up to 1.0"
            % (frac_train, frac_val, frac_test)
        )
    if stratify_colname not in df_input.columns:
        raise ValueError("%s is not a column in the dataframe" % (stratify_colname))
    X = df_input  # Contains all columns.
    y = df_input[
        [stratify_colname]
    ]  # Dataframe of just the column on which to stratify.
    # Split original dataframe into train and temp dataframes.
    df_train, df_temp, y_train, y_temp = train_test_split(
        X, y, stratify=y, test_size=(1.0 - frac_train), random_state=random_state
    )
    if frac_val <= 0:
        assert len(df_input) == len(df_train) + len(df_temp)
        return df_train, pd.DataFrame(), df_temp, y_train, pd.DataFrame(), y_temp
    # Split the temp dataframe into val and test dataframes.
    relative_frac_test = frac_test / (frac_val + frac_test)
    df_val, df_test, y_val, y_test = train_test_split(
        df_temp,
        y_temp,
        stratify=y_temp,
        test_size=relative_frac_test,
        random_state=random_state,
    )
    assert len(df_input) == len(df_train) + len(df_val) + len(df_test)
    return df_train, df_val, df_test, y_train, y_val, y_test

X_train, X_val, X_test, y_train, y_val, y_test = split_stratified_into_train_val_test(
    df, stratify_colname="Age", frac_train=0.80, frac_val=0, frac_test=0.20, random_state=None
)

display("X_train", X_train)
display("y_train", y_train)

display("X_test", X_test)
display("y_test", y_test)

NameError: name 'df_transformed' is not defined